In [1]:
!pip install pythainlp
!pip install -q simpletransformers
!pip install kmedoids
!pip install torch-hd

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.9/17.9 MB 60.6 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 454.6/454.6 kB 3.2 MB/s eta 0:00:00a 0:00:01m
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 351.0/351.0 kB 2.5 MB/s eta 0:00:00a 0:00:01m


In [2]:
import pandas as pd
train_df = pd.read_csv("/kaggle/input/super-ai-season-4-community-extractive-qa/extract_qa_train.csv")
test_df = pd.read_csv("/kaggle/input/super-ai-season-4-community-extractive-qa/extract_qa_test_fix3.csv")
val_df = pd.read_csv("/kaggle/input/super-ai-season-4-community-extractive-qa/extract_qa_val.csv")

In [3]:
train_df

question_id            article_id  \
0     01KZTrxgvC5mOovXFMPJ_000  01KZTrxgvC5mOovXFMPJ   
1     01KZTrxgvC5mOovXFMPJ_001  01KZTrxgvC5mOovXFMPJ   
2     01KZTrxgvC5mOovXFMPJ_002  01KZTrxgvC5mOovXFMPJ   
3     01KZTrxgvC5mOovXFMPJ_003  01KZTrxgvC5mOovXFMPJ   
4     01asKzWKkocCMjZAITfL_001  01asKzWKkocCMjZAITfL   
...                        ...                   ...   
5756  zwjbY823xEbkAn995Ho3_000  zwjbY823xEbkAn995Ho3   
5757  zwjbY823xEbkAn995Ho3_001  zwjbY823xEbkAn995Ho3   
5758  zx9Q54MmAFpODs5j6eQr_000  zx9Q54MmAFpODs5j6eQr   
5759  zx9Q54MmAFpODs5j6eQr_001  zx9Q54MmAFpODs5j6eQr   
5760  zx9Q54MmAFpODs5j6eQr_004  zx9Q54MmAFpODs5j6eQr   

                              title  \
0          พัทธ์ธีรา ศรุติพงศ์โภคิน   
1          พัทธ์ธีรา ศรุติพงศ์โภคิน   
2          พัทธ์ธีรา ศรุติพงศ์โภคิน   
3          พัทธ์ธีรา ศรุติพงศ์โภคิน   
4                        คลีโอพัตรา   
...                             ...   
5756  ความลำเอียงทางเพศบนวิกิพีเดีย   
5757  ความลำเอียงทางเพศบนวิกิพีเดีย   
5758                       ปลาตะกาก   
5759                       ปลาตะกาก   
5760                       ปลาตะกาก   

                                                context  \
0     พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
1     พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
2     พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
3     พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
4     คลีโอพัตราที่ 7 ฟิโลพาเธอร์ (กรีก: Κλεοπάτρα θ...   
...                                                 ...   
5756  "ผู้แก้ไข [วิกิพีเดีย] ส่วนใหญ่เป็นชายหนุ่มที่...   
5757  "ผู้แก้ไข [วิกิพีเดีย] ส่วนใหญ่เป็นชายหนุ่มที่...   
5758  ปลาตะกาก เป็นปลาน้ำจืดชนิดหนึ่ง มีชื่อวิทยาศาส...   
5759  ปลาตะกาก เป็นปลาน้ำจืดชนิดหนึ่ง มีชื่อวิทยาศาส...   
5760  ปลาตะกาก เป็นปลาน้ำจืดชนิดหนึ่ง มีชื่อวิทยาศาส...   

                                               question  \
0             พัทธ์ธีรา ศรุติพงศ์โภคิน เกิดวันที่เท่าไร   
1            พัทธ์ธีรา ศรุติพงศ์โภคิน มีฃื่อเล่นว่าอะไร   
2                  พัทธ์ธีรา ศรุติพงศ์โภคิน ทำอาชีพอะไร   
3      พัทธ์ธีรา ศรุติพงศ์โภคิน จบการศึกษาจากประเทศอะไร   
4                              บิดาของคลีโอพัตราเป็นใคร   
...                                                 ...   
5756  จำนวนผู้หญิงที่แก้ไขข้อมูลบนวิกิพีเดียคิดเป็นร...   
5757  จำนวนผู้หญิงสหรัฐที่แก้ไขข้อมูลบนวิกิพีเดียคิด...   
5758        ปลาตะกากมีชื่อเรียกทางวิทยาศาสตร์ว่าอย่างไร   
5759      ปลาตะกากถือว่าเป็นปลาน้ำจืดที่จัดอยู่ในวงศ์ใด   
5760  ปลาตะกากมักพบเลี้ยงเป็นปลาสวยงามมีชื่อในวงการว...   

                                                answers  
0     {'text': array(['3 ธันวาคม พ.ศ. 2533'], dtype=...  
1     {'text': array(['อร'], dtype=object), 'answer_...  
2     {'text': array(['นักแสดงหญิงชาวไทย'], dtype=ob...  
3     {'text': array(['ประเทศนิวซีแลนด์'], dtype=obj...  
4     {'text': array(['ทอเลมีที่ 12 ออเลติส'], dtype...  
...                                                 ...  
5756  {'text': array(['8.5 – 16'], dtype=object), 'a...  
5757  {'text': array(['22.7%'], dtype=object), 'answ...  
5758  {'text': array(['ชื่อวิทยาศาสตร์ว่า Cosmochilu...  
5759  {'text': array(['วงศ์ปลาตะเพียน (Cyprinidae)']...  
5760  {'text': array(['กระมังครีบสูง'], dtype=object...  

[5761 rows x 6 columns]

In [4]:
import pandas as pd
import re
import ast
def clean_and_convert(answer_str):
    # Remove 'array(...)' and 'dtype=...' parts using regular expressions
    clean_str = re.sub(r"array\(|, dtype=object|\)|, dtype=int32|,\n\s*dtype=object", "", answer_str)
    # Evaluate the cleaned string to a dictionary
    parsed_dict = ast.literal_eval(clean_str)
    return parsed_dict

In [5]:
train_df['answers'] = train_df['answers'].apply(clean_and_convert)
val_df['answers'] = val_df['answers'].apply(clean_and_convert)

In [6]:
train_df['answers'] = train_df['answers'].to_dict()
val_df['answers'] = val_df['answers'].to_dict()

In [7]:
import json
from pythainlp.tokenize import word_tokenize

In [8]:
def convert_to_simpletransformer_format(df):
  all = {}
  for (idx, row) in df.iterrows():
    # print(row)
    answers = row["answers"]
    if (row["article_id"] not in all):
      all[row["article_id"]] = {"context": " ".join(word_tokenize(row['context'],engine="newmm-safe")), "qas":[]}
    question_text = " ".join(word_tokenize(row['question'],engine="newmm-safe"))
    answer_text = " ".join(word_tokenize(answers["text"][0],engine="newmm-safe"))
    try:
      answer_start = all[row["article_id"]]["context"].index(answer_text)
      all[row["article_id"]]["qas"].append({"id":row["question_id"], "is_impossible": False, "question": question_text, "answers": [{"text":answer_text, "answer_start": answer_start}]})
    except Exception as e:
      print("Context:" +all[row["article_id"]]["context"])
      print("Answer:" +answer_text)
      print("Exception:" +str(e))
  return list(all.values())

In [9]:
import logging
import torch

from simpletransformers.question_answering import QuestionAnsweringModel, QuestionAnsweringArgs

logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

train = convert_to_simpletransformer_format(train_df)
val = convert_to_simpletransformer_format(val_df)

2024-06-11 06:55:16.832322: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-06-11 06:55:16.832449: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-06-11 06:55:16.960532: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


Context:พัทธ์ ธี รา   ศรุติ พงศ์ โภคิน   ( เกิด   3   ธันวา ค ม   พ.ศ.   2533 )   หรือ ชื่อเล่น ว่า   อร   เป็น นัก แ สด ง หญิง ชาวไทย   สำเร็จ มัธยมศึกษา จาก Cat holic   Cathedral   College   ประเทศ นิว ซี แล นด์   และ ปริญญาตรี จาก Raffles   International   College   สาขา   Business   Marketing 
 
 เข้า สู ่ วงการ ตั้งแต่ อายุ   6   ขวบ   จาก การแสดง ละ คร เวที กับ   ครู ชล ประคัลภ์   จันทร์ เรือง   จากนั้น ก็ เล่น โฆษณา ใน วัยเด็ก   2 -   3   ช ิ้น   และ ยัง เคย แสดง ช่วง ละคร สั้น   ใน ร าย การ ซุปเปอร์ จิ๋ว   ประมาณ ปี   2542 
 
 ปัจจุบัน เป็น ทั้ง   นักแสดง   ,   พิธีกร   และ   ว ี เจ   อยู่ ที่ คลื่น   เก็ท   102.5   Bangkok   International   Hits   Music   Station   และ ยัง เป็น พิธีกร ให้ กับ ช่อง   ทรู   มิวสิก
Answer:3   ธันวาคม   พ.ศ.   2533
Exception:substring not found
Context:พัทธ์ ธี รา   ศรุติ พงศ์ โภคิน   ( เกิด   3   ธันวา ค ม   พ.ศ.   2533 )   หรือ ชื่อเล่น ว่า   อร   เป็น นัก แ สด ง หญิง ชาวไทย   สำเร็จ มัธยมศึกษา จาก Cat holic   Cathedral   College   ประเทศ นิว ซี

In [10]:
# Configure the model
model_args = QuestionAnsweringArgs()
model_args.train_batch_size = 200
model_args.n_best_size = 1
#max_query_length = 128
model_args.evaluate_during_training = True
model_args.save_model_every_epoch = False
model_args.overwrite_output_dir = True
model_args.num_train_epochs = 40

model = QuestionAnsweringModel(
    "camembert", "airesearch/wangchanberta-base-att-spm-uncased", args=model_args, use_cuda=torch.cuda.is_available()
)

# Train the model
model.train_model(train, eval_data=val)

# Evaluate the model
# result, texts = model.eval_model(val)
import torch, gc
gc.collect()
torch.cuda.empty_cache()

/opt/conda/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/546 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/423M [00:00<?, ?B/s]

Some weights of CamembertForQuestionAnswering were not initialized from the model checkpoint at airesearch/wangchanberta-base-att-spm-uncased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


tokenizer_config.json:   0%|          | 0.00/282 [00:00<?, ?B/s]

...


convert squad examples to features: 100%|██████████| 561/561 [00:03<00:00, 171.03it/s]

add example index and unique id: 100%|██████████| 561/561 [00:00<00:00, 352140.76it/s]


Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

Running Epoch 40 of 40:   0%|          | 0/37 [00:00<?, ?it/s]


convert squad examples to features: 100%|██████████| 561/561 [00:03<00:00, 172.24it/s]

add example index and unique id: 100%|██████████| 561/561 [00:00<00:00, 435580.26it/s]


Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

In [28]:
!ls

cache_dir  outputs  runs


In [33]:
import torch, gc
gc.collect()
torch.cuda.empty_cache()

In [34]:
test_df

title  \
0                                 ลูพิน   
1                            ปลากัดช้าง   
2    กีฬาสกีลงเขาในโอลิมปิกฤดูหนาว 2018   
3       เจ้าชายฟิลิแบร์โต ดยุกแห่งเจนัว   
4                               ไอซ์วัน   
..                                  ...   
734                 ชดช้อย ใหม่เมืองคอน   
735     โครงการหนึ่งตำบล หนึ่งผลิตภัณฑ์   
736                             เอสิกส์   
737                    เอ็ดเวิร์ด มโพฟู   
738                        ปลากะพงเขียว   

                                               context  \
0    ลูพิน (อังกฤษ: Lupin หรือ lupine) เป็นพืชดอกที...   
1    ปลากัดช้าง หรือ ปลากัดน้ำแดง (ชื่อวิทยาศาสตร์:...   
2    กีฬาสกีลงเขาในโอลิมปิกฤดูหนาว 2018 เป็นการแข่ง...   
3    เจ้าชายฟิลิแบร์โต ดยุกแห่งเจนัว (อังกฤษ: Princ...   
4    ไอซ์วัน (อังกฤษ: IZ*ONE; เกาหลี: 아이즈원 อาอีจือว...   
..                                                 ...   
734  ชดช้อย ใหม่เมืองคอนหรือนักมวยไทยชื่อดัง ชดช้อย...   
735  โครงการหนึ่งตำบล หนึ่งผลิตภัณฑ์ (อังกฤษ: One T...   
736  เอสิกส์ (อังกฤษ: ASICS) ตราสินค้าผลิตภัณฑ์กีฬา...   
737  มโพฟูขึ้นชกมวยสากลครั้งแรกเมื่อ 29 มีนาคม พ.ศ....   
738  ปลากะพงเขียว (อังกฤษ: Blue-gray snapper, Green...   

                                              question   id  
0                                   ลูพิน อยู่ในวงอะไร    0  
1                ปลากัดช้างมีชื่อทางวิทยาศาสตร์ว่าอะไร    1  
2    ารแข่งขันกีฬาเคอร์ลิงครั้งนี้มีการแข่งขันทั้งห...    2  
3     เจ้าชายฟิลิแบร์โต ดยุกแห่งเจนัว ทรงเสกสมรสกับใคร    3  
4                         ชื่อแฟนคลับของไอซ์วันคืออะไร    4  
..                                                 ...  ...  
734                          ชดช้อย ใหม่เมืองคอนคือใคร  734  
735     โครงการหนึ่งตำบล หนึ่งผลิตภัณฑ์เรียกย่อว่าอะไร  735  
736                           ก่อตั้งขึ้นเมื่อวันที่ ?  736  
737    เอ็ดเวิร์ด มโพฟู ชกมวยครั้งแรกเมื่อวันที่เท่าไร  737  
738              ปลากะพงเขียว มีน้ำหนักมากที่สุดเท่าไร  738  

[739 rows x 4 columns]

In [35]:
# Create the list of dictionaries
to_predict = []
for _, row in test_df.iterrows():
    qas = [{"question": row['question'], "id": str(row['id'])}]
    to_predict.append({"context": row['context'], "qas": qas})

In [36]:
answers, probabilities = model.predict(to_predict)

/opt/conda/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()
add example index and unique id: 100%|██████████| 739/739 [00:00<00:00, 540846.39it/s]


Running Prediction:   0%|          | 0/9 [00:00<?, ?it/s]

In [37]:
df = pd.DataFrame(answers)

In [38]:
df

id                                             answer
0      0  [เป็นพืชดอกที่อยู่ในสกุลลูพินนัส (Lupinus) ในว...
1      1                                        [Betta pi)]
2      2                                        [11 รายการ]
3      3                 [กับเจ้าหญิงอิซาเบลลาแห่งบาวาเรีย]
4      4                                            [empty]
..   ...                                                ...
734  734  [ในสังกัดของใหม่ เมืองคอน เมื่อใหม่ เมืองคอนได...
735  735                                            [โอทอป]
736  736                              [1 กันยายน ค.ศ. 1949]
737  737                              [29 มีนาคม พ.ศ. 2541]
738  738                                            [empty]

[739 rows x 2 columns]

In [42]:
dfp = pd.DataFrame(probabilities)

In [43]:
dfp

id            probability
0      0   [0.9999993376950417]
1      1   [0.9999999999971674]
2      2    [0.999999999999996]
3      3   [0.9998427581691118]
4      4   [0.9961230735302391]
..   ...                    ...
734  734   [0.9878293708042446]
735  735   [0.9999999996832938]
736  736    [0.999999999999998]
737  737   [0.9999999997440241]
738  738  [0.02595735719779685]

[739 rows x 2 columns]

In [44]:
df['probabilities'] = dfp['probability']

In [48]:
df['answer'][0]

['เป็นพืชดอกที่อยู่ในสกุลลูพินนัส (Lupinus) ในวงศ์ถั่วที่มีด้วยกันทั้งหมดราว']

In [19]:
df['probabilities'][0]

[0.9999993376950417]

In [46]:
# Example lists
max_answer =[]
for i in range(739):
    max_index = df['probabilities'][i].index(max(df['probabilities'][i]))
    # Get the corresponding answer
    max_answer.append(df['answer'][i][max_index])

In [47]:
max_answer

['เป็นพืชดอกที่อยู่ในสกุลลูพินนัส (Lupinus) ในวงศ์ถั่วที่มีด้วยกันทั้งหมดราว',
 'Betta pi)',
 '11 รายการ',
 'กับเจ้าหญิงอิซาเบลลาแห่งบาวาเรีย',
 'empty',
 'empty',
 'วงศ์ปลาข้างใส',
 'พ.ศ. 2401',
 'empty',
 'empty',
 'One Village, One Product',
 '12 กุมภาพันธ์ พ.ศ. 2562',
 'empty',
 'เป็นซิงเกิลเปิดตัวของวงเอ็มทูเอ็ม ดูโอแนวป็อปจากนอร์เวย์ที่ประกอบด้วยสมาชิกคือ',
 'ขนาด W1830 x H2440 หนา 12 mm.',
 'ขนาด W1830 x H2440 หนา 12 mm.',
 'empty',
 'empty',
 'ศ',
 'empty',
 'ศ',
 'นักแสดงหญิง',
 'empty',
 'เป็นโรงเรียนสถานศึกษาขนาดกลางระดับมัธยมศึกษา',
 'มีชื่อวิทยาศาสตร์ว่า Hemibagrus filamentus',
 'Devsisters',
 'empty',
 'empty',
 '2,000 กิโลแคลอรี',
 'empty',
 'empty',
 'เป็นตัวละครการ์ตูนซูเปอร์ฮีโรที่ปรากฏในหนังสือการ์ตูนของดีซีคอมิกส์',
 'empty',
 'คือภาพยนตร์อเมริกันแนวดราม่า',
 'เป็นนักร้องชาวอเมริกัน',
 '"จีน" แฮกแมน (อังกฤษ: Eugene Allen "Gene" Hackman)[1] เกิดเมื่อวันที่ 30 มกราคม ค.ศ. 1930 เป็นนักแสดงชายชาวอเมริกัน',
 'เมืองไทนิสได้เริ่มเสื่อมความสำคัญลงในราชวงศ์ที่สาม',
 'โดยมีระ

In [22]:
cd /kaggle/input/hypersum

[Errno 2] No such file or directory: '/kaggle/input/hypersum'
/kaggle/working


In [49]:
from hypersum import Summarizer 
summarizer = Summarizer()

ModuleNotFoundError: No module named 'hypersum'

In [ ]:
for i in range(739):
    df['answer'][i] = summarizer.summarize(df['answer'][i],1)
    df['answer'][i] = df['answer'][i][0]

In [ ]:
df['answer']

In [52]:
sub = pd.read_csv("/kaggle/input/super-ai-season-4-community-extractive-qa/extract_qa_sample_submission.csv")

In [53]:
sub

id                                             answer
0      0  วงศ์ถั่วที่มีด้วยกันทั้งหมดราว 200 ถึง 600 สปี...
1      1                          ชื่อวิทยาศาสตร์: Betta pi
2      2                      มีการแข่งขันทั้งหมด 11 รายการ
3      3                    เจ้าหญิงลิเดียร์แห่งแอเทนเบิร์ก
4      4                                                NaN
..   ...                                                ...
734  734                                                NaN
735  735                                                NaN
736  736                                                NaN
737  737                                                NaN
738  738                                                NaN

[739 rows x 2 columns]

In [54]:
sub['answer'].loc[4:] = df['answer'].loc[4:]

/tmp/ipykernel_34/4214206180.py:1: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  sub['answer'].loc[4:] = df['answer'].loc[4:]
/tmp/ipykernel_34/4214206180.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a

In [55]:
sub

id                                             answer
0      0  วงศ์ถั่วที่มีด้วยกันทั้งหมดราว 200 ถึง 600 สปี...
1      1                          ชื่อวิทยาศาสตร์: Betta pi
2      2                      มีการแข่งขันทั้งหมด 11 รายการ
3      3                    เจ้าหญิงลิเดียร์แห่งแอเทนเบิร์ก
4      4                                            [empty]
..   ...                                                ...
734  734  [ในสังกัดของใหม่ เมืองคอน เมื่อใหม่ เมืองคอนได...
735  735                                            [โอทอป]
736  736                              [1 กันยายน ค.ศ. 1949]
737  737                              [29 มีนาคม พ.ศ. 2541]
738  738                                            [empty]

[739 rows x 2 columns]

In [ ]:
import pandas as pd

In [57]:
pwd

'/kaggle/working/outputs/best_model'

In [ ]:
import os
os.mkdir('/kaggle/working/mainfolder/')
os.chdir("/kaggle/working/mainfolder/")

In [56]:
sub.to_csv("submission.csv",index = False)

In [ ]:
import os
os.mkdir('/kaggle/working/mainfolder/')
os.chdir("/kaggle/working/mainfolder/")